In [1]:
import os
import pickle

import eli5
import numpy as np
import pandas as pd
import shap
from IPython.display import clear_output, display
from lime.lime_tabular import LimeTabularExplainer
from pycaret import classification

shap.initjs()


# Load Dataset

In [2]:
tmp = pd.read_csv("datasets/GSE2109_Breast/GSE2109_Breast.txt", delimiter="\t")
tmp.columns = ["SampleID"] + [x for x in tmp.columns[1:]]
tmp_clinical = pd.read_csv(
    "datasets/GSE2109_Breast/GSE2109_Breast_Clinical.txt", delimiter="\t"
)
tmp_y = pd.read_csv(
    "datasets/GSE2109_Breast/Class/MolecularMarker__HER2_Neu.txt", delimiter="\t"
)


In [3]:
tmp.sort_values(by="SampleID", inplace=True)
tmp.reset_index(drop=True, inplace=True)
tmp.head(5)


SampleID  ENSG00000000003  ENSG00000000005  ENSG00000000419  \
0  GSM102440         0.566591        -0.219697         2.733392   
1  GSM102441         0.921192        -0.169056         1.900753   
2  GSM102468         0.972782        -0.126902         3.326847   
3  GSM102482         3.376839        -0.274193         1.902793   
4  GSM102487         0.327419        -0.185059         1.981205   

   ENSG00000000457  ENSG00000000460  ENSG00000000938  ENSG00000000971  \
0         0.563140         0.200046         0.283661         0.473756   
1         0.514206         0.122097         0.313717         0.616491   
2         0.377566         0.094843         0.204581         0.034419   
3         0.496311         0.159335         0.008204         0.186353   
4         0.585194         0.143971         0.326530         0.368505   

   ENSG00000001036  ENSG00000001084  ENSG00000001167  ENSG00000001460  \
0         0.431626         0.388042         0.253845         0.061607   
1         0.720333         0.429962         0.235544        -0.044600   
2         0.740314         0.385903         0.201403         0.070238   
3         0.530787         0.293708         0.135811         0.087551   
4         0.736161         0.386557         0.229643         0.200715   

   ENSG00000001461  ENSG00000001497  ENSG00000001561  ENSG00000001617  \
0         0.289322         0.560610         0.741437         1.050979   
1         0.206667         0.464350         1.079877         0.599524   
2         0.319025         0.415593         0.555906         0.672570   
3         0.415841         0.399750         0.553649         0.965983   
4         0.845521         0.396058         0.666303         0.997223   

   ENSG00000001626  ENSG00000001629  ENSG00000001631  ENSG00000002016  \
0        -0.175941         1.860842         0.398094        -0.140709   
1        -0.258189         1.276488         0.001719        -0.196893   
2        -0.147212         1.586426         0.138298        -0.134306   
3        -0.142365         1.349503         0.052409        -0.141023   
4        -0.170116         1.748195         0.321865        -0.171218   

   ENSG00000002079  ENSG00000002330  ENSG00000002549  ENSG00000002586  \
0         0.275972         0.365059         2.194035         1.340416   
1         0.525949         0.046051         2.081684         2.066535   
2         0.297654         0.221937         1.639809         1.596821   
3         0.552351         0.081433         1.473531         0.758137   
4         0.395205         0.134900         2.169878         1.658307   

   ENSG00000002587  ENSG00000002726  ENSG00000002745  ENSG00000002746  \
0        -0.102555        -0.239106        -0.149661        -0.025625   
1        -0.033527        -0.131395        -0.179747        -0.017309   
2        -0.062652        -0.131492        -0.028097        -0.065658   
3        -0.210278        -0.156678        -0.001419         0.002162   
4         0.033987        -0.125823        -0.122038        -0.109017   

   ENSG00000002822  ENSG00000002834  ENSG00000002919  ENSG00000002933  \
0         0.079315         1.771884         0.574754         1.028439   
1         0.008593         2.122270         0.619033         1.248110   
2         0.240672         2.406869         0.459482         0.923148   
3        -0.129141         2.255408         0.404038         0.568257   
4        -0.117490         2.542988         0.934796         0.553534   

   ENSG00000003056  ENSG00000003096  ENSG00000003137  ENSG00000003147  \
0         0.766052         0.011416        -0.330508         0.062105   
1         0.624450         0.142053        -0.218385         0.050762   
2         1.171245         0.071562        -0.219407         0.230010   
3         0.505544        -0.130421        -0.196329         0.277306   
4         0.962054        -0.017640        -0.140618         0.218637   

   ENSG00000003249  ENSG00000003393  ENSG00000003400  ENSG00000003402  \
0         0.1350

In [4]:
tmp_clinical.sort_values(by="SampleID", inplace=True)
tmp_clinical.reset_index(drop=True, inplace=True)
tmp_clinical.head(5)


SampleID Alcohol_Consumption Clinical_ER  Clinical_Grade  \
0  GSM102439                 Yes         NaN             NaN   
1  GSM102440                  No         NaN             NaN   
2  GSM102441                  No         NaN             NaN   
3  GSM102468                  No         NaN             NaN   
4  GSM102482                  No         NaN             NaN   

  Clinical_HER2_Neu  Clinical_M Clinical_Metastatic_Sites  \
0               NaN         NaN                       NaN   
1               NaN         NaN                       NaN   
2               NaN         NaN                       NaN   
3               NaN         NaN                       NaN   
4               NaN         NaN                       NaN   

  Clinical_Multiple_Tumors Clinical_N Clinical_PR Clinical_Stage  \
0                      NaN        NaN         NaN            NaN   
1                      NaN        NaN         NaN            NaN   
2                      NaN        NaN         NaN            NaN   
3                      NaN        NaN         NaN            NaN   
4                      NaN        NaN         NaN            NaN   

  Clinical_Stage_During_or_Following_Multimodality_Therapy Clinical_T  \
0                                                NaN              NaN   
1                                                NaN              NaN   
2                                                NaN              NaN   
3                                                NaN              NaN   
4                                                NaN              NaN   

   Days_from_Patient_Diagnosis_to_Excision   ER Ethnic_Background  \
0                                    110.0  NaN         Caucasian   
1                                     30.0  NaN  African-American   
2                                     35.0  NaN         Caucasian   
3                                     15.0  NaN  African-American   
4                                     21.0  NaN         Caucasian   

  Family_History_of_Cancer Fibrocystic_disease  Gender HER2_Neu  \
0                      Yes                  No  Female      NaN   
1                       No                  No  Female      NaN   
2                      Yes                  No  Female      NaN   
3                      Yes                 NaN  Female      NaN   
4                      Yes                  No  Female      NaN   

                        Histology Hormonal_therapy_Number_of_Years Mammogram  \
0  Metaplastic squamous carcinoma                              NaN       Yes   
1                Ductal Carcinoma                              NaN       Yes   
2                Ductal Carcinoma                              NaN       Yes   
3                Ductal Carcinoma                              NaN       Yes   
4               Lobular Carcinoma                             6-10       Yes   

  Mammogram_calcifications Multiple_Tumors  \
0                      NaN             NaN   
1                       No             NaN   
2                       No             NaN   
3                      NaN             NaN   
4                       No             NaN   

  Number_of_years_in_which_a_mammogram_was_obtained  \
0                                               0-5   
1                                               0-5   
2                                             11-15   
3                                               0-5   
4                                             16-20   

  Number_of_years_of_use_Oral_contraceptives Number_of_Years_Until_Relapse  \
0                                        NaN                           NaN   
1                                        NaN                           NaN   
2                                        NaN                           NaN   
3                                        NaN                           NaN   
4                                        NaN                           NaN   

  Oophorectomy Oral_contrace

In [5]:
tmp_y.sort_values(by="SampleID", inplace=True)
tmp_y.reset_index(drop=True, inplace=True)
# tmp_y["Class"][tmp_y["Class"] == "Negative"] = 0
# tmp_y["Class"][tmp_y["Class"] == "Positive"] = 1
tmp_y.head(5)


SampleID     Class
0  GSM102440  Negative
1  GSM102468  Negative
2  GSM102499  Positive
3  GSM102506  Negative
4  GSM102523  Negative

In [6]:
new_tmp = tmp.merge(tmp_y, on="SampleID")
new_tmp = new_tmp[new_tmp.columns[1:]]
new_tmp


ENSG00000000003  ENSG00000000005  ENSG00000000419  ENSG00000000457  \
0           0.566591        -0.219697         2.733392         0.563140   
1           0.972782        -0.126902         3.326847         0.377566   
2           1.074197        -0.125940         2.419111         0.432723   
3           1.362664        -0.203689         2.367200         0.383531   
4           1.229762        -0.169097         2.584839         0.671984   
5           1.760115         0.008868         2.551409         0.780634   
6           0.950663        -0.275112         3.514400         0.559187   
7           0.565794        -0.143721         2.248740         0.538802   
8           1.825373         0.247663         2.413483         0.239732   
9           1.132255         0.833285         1.869616         0.378512   
10          0.462426        -0.297790         2.666856         0.586875   
11          1.814861        -0.100165         2.191276         0.686563   
12          1.345595         1.345193         2.143317         0.272193   
13          1.168540        -0.085781         2.577023         0.543890   
14          0.949795        -0.149336         1.989558         0.894266   
15          0.853863        -0.220110         2.998355         0.614370   
16          0.640773        -0.038825         2.082953         1.106504   
17          1.744039        -0.172025         2.434642         0.327298   
18          0.975733        -0.246201         1.959303         0.650586   
19          0.900194        -0.261535         2.810729         0.425865   
20          0.433197        -0.158174         2.476650         0.588694   
21          1.534398        -0.025260         2.329123         0.406396   
22          1.757171        -0.122307         2.456274         0.686398   
23          0.072925        -0.244626         2.772076         0.612274   
24          1.047915        -0.076786         2.092358         0.458325   
25          0.969624        -0.163400         2.970769         0.736338   
26          0.842827        -0.143084         2.450584         0.445086   
27          1.482949         0.650202         2.057671         0.662407   
28          0.718422        -0.147786         1.983358         0.715858   
29          0.741260        -0.100051         2.092509         0.362445   
30          1.286092         0.259652         2.549742         0.354064   
31          0.871225        -0.118713         2.455727         0.431949   
32          1.049050        -0.177673         2.290617         0.929306   
33          1.277524        -0.215720         3.045640         0.452576   
34          0.605798        -0.017024         1.988597         0.645313   
35          0.707089        -0.094269         1.598718         0.429206   
36          1.362879        -0.137352         2.000562         0.374881   
37          0.636180         0.048332         1.903217         0.600672   
38          1.259206        -0.203305         2.602867         0.579480   
39          1.117287        -0.287009         1.945551         0.713832   
40          1.300543         0.124456         2.476039         0.456683   
41          0.957125        -0.186079         2.259384         0.333910   
42          0.867480        -0.066716         1.962361         0.211797   
43          0.669488        -0.123035         1.243338         0.292903   
44          0.369691        -0.346706         2.118749         0.205088   
45          0.902487        -0.260376         2.758597         0.413075   
46          1.630735        -0.039729         2.235919         0.392873   
47          0.554947        -0.185766         2.067794         0.383499   
48          1.008916        -0.246653         2.375291         0.608635   
49          1.284955        -0.119036         2.330636         0.488683   
50          1.132512         0.477443         2.734831         0.393497   
51          1.147447        -0.326960         2.437593         0.672360   
52          1.733623        -0

# Setup Pycaret

In [7]:
# skip to load data/models if you already have the .pkl files
classification.setup(
    data=new_tmp,
    target="Class",
    train_size=0.75,
    silent=True,
    verbose=True,
    preprocess=False,
    session_id=666,
    fold_shuffle=True,
)


({'parameter': 'Hyperparameters',
  'auc': 'AUC',
  'confusion_matrix': 'Confusion Matrix',
  'threshold': 'Threshold',
  'pr': 'Precision Recall',
  'error': 'Prediction Error',
  'class_report': 'Class Report',
  'rfe': 'Feature Selection',
  'learning': 'Learning Curve',
  'manifold': 'Manifold Learning',
  'calibration': 'Calibration Curve',
  'vc': 'Validation Curve',
  'dimension': 'Dimensions',
  'feature': 'Feature Importance',
  'feature_all': 'Feature Importance (All)',
  'boundary': 'Decision Boundary',
  'lift': 'Lift Chart',
  'gain': 'Gain Chart',
  'tree': 'Decision Tree'},
 10,
      ENSG00000000003  ENSG00000000005  ENSG00000000419  ENSG00000000457  \
 0           0.566591        -0.219697         2.733392         0.563140   
 1           0.972782        -0.126902         3.326847         0.377566   
 2           1.074197        -0.125940         2.419111         0.432723   
 3           1.362664        -0.203689         2.367200         0.383531   
 4           1.2297

# Save Data

In [8]:
with open("./split_datasets/X_train.pkl", "wb") as f:
    pickle.dump(classification.get_config("X_train"), f, pickle.HIGHEST_PROTOCOL)

with open("./split_datasets/X_test.pkl", "wb") as f:
    pickle.dump(classification.get_config("X_test"), f, pickle.HIGHEST_PROTOCOL)

with open("./split_datasets/Y_train.pkl", "wb") as f:
    pickle.dump(classification.get_config("y_train"), f, pickle.HIGHEST_PROTOCOL)

with open("./split_datasets/Y_test.pkl", "wb") as f:
    pickle.dump(classification.get_config("y_test"), f, pickle.HIGHEST_PROTOCOL)


# Create Models

In [9]:
# exclude catboost as it is too RAM intensive
my_models = classification.compare_models(exclude=["catboost"], n_select=100)


# Save Models

In [10]:
for i, m in enumerate(my_models):
    classification.save_model(m, f"./models/{i:02}_{str(type(m))[8:-2]}")


Transformation Pipeline and Model Succesfully Saved
Transformation Pipeline and Model Succesfully Saved
Transformation Pipeline and Model Succesfully Saved
Transformation Pipeline and Model Succesfully Saved
Transformation Pipeline and Model Succesfully Saved
Transformation Pipeline and Model Succesfully Saved
Transformation Pipeline and Model Succesfully Saved
Transformation Pipeline and Model Succesfully Saved
Transformation Pipeline and Model Succesfully Saved
Transformation Pipeline and Model Succesfully Saved
Transformation Pipeline and Model Succesfully Saved
Transformation Pipeline and Model Succesfully Saved
Transformation Pipeline and Model Succesfully Saved
Transformation Pipeline and Model Succesfully Saved


# Load Data

In [7]:
with open("./split_datasets/X_train.pkl", "rb") as f:
    X_train = pickle.load(f)

with open("./split_datasets/X_test.pkl", "rb") as f:
    X_test = pickle.load(f)

with open("./split_datasets/Y_train.pkl", "rb") as f:
    Y_train = pd.DataFrame(pickle.load(f))

with open("./split_datasets/Y_test.pkl", "rb") as f:
    Y_test = pd.DataFrame(pickle.load(f))


# Load Models

In [8]:
my_models = list()
for p in os.listdir("./models/"):
    if p == ".gitignore":
        continue

    print(p)
    my_models.append(classification.load_model(f"./models/{p[:-4]}"))


00_lightgbm.sklearn.LGBMClassifier.pkl
Transformation Pipeline and Model Successfully Loaded
01_sklearn.linear_model._ridge.RidgeClassifier.pkl
Transformation Pipeline and Model Successfully Loaded
02_sklearn.linear_model._logistic.LogisticRegression.pkl
Transformation Pipeline and Model Successfully Loaded
03_xgboost.sklearn.XGBClassifier.pkl
Transformation Pipeline and Model Successfully Loaded
04_sklearn.neighbors._classification.KNeighborsClassifier.pkl
Transformation Pipeline and Model Successfully Loaded
05_sklearn.naive_bayes.GaussianNB.pkl
Transformation Pipeline and Model Successfully Loaded
06_sklearn.discriminant_analysis.LinearDiscriminantAnalysis.pkl
Transformation Pipeline and Model Successfully Loaded
07_sklearn.ensemble._gb.GradientBoostingClassifier.pkl
Transformation Pipeline and Model Successfully Loaded
08_sklearn.ensemble._weight_boosting.AdaBoostClassifier.pkl
Transformation Pipeline and Model Successfully Loaded
09_sklearn.linear_model._stochastic_gradient.SGDCla

In [9]:
Y_test.iloc[0], Y_test.iloc[7]


(Class    0
 Name: 104, dtype: int64,
 Class    1
 Name: 22, dtype: int64)

# LIME

## Visualizations

In [ ]:
explainer = LimeTabularExplainer(
    X_train.values,
    training_labels=Y_train.values,
    feature_names=X_train.columns,
    class_names=["Negative", "Positive"],
    random_state=666,
)
for pre, model in my_models:
    if not hasattr(model, "predict_proba"):
        continue

    for i in (5, 10, 25):
        clear_output(wait=True)
        exp_neg = explainer.explain_instance(
            X_test.iloc[0], model.predict_proba, num_samples=i
        )
        print(f"Model: {str(type(model))[8:-2]}\nSamples: {i}")
        print("Negative")
        exp_neg.show_in_notebook(show_all=True)
        exp_pos = explainer.explain_instance(
            X_test.iloc[7], model.predict_proba, num_samples=i
        )
        print("Positive")
        exp_pos.show_in_notebook(show_all=True)
        input("Just enjoy the results and press enter to continue")


## Stats

In [ ]:
# don't run this cell, it may take days to complete
explainer = LimeTabularExplainer(
    X_train.values,
    training_labels=Y_train.values,
    feature_names=X_train.columns,
    class_names=["Negative", "Positive"],
    random_state=666,
)
counter = dict()
for pre, model in my_models:
    counter[str(type(model))[8:-2]] = dict()
    if not hasattr(model, "predict_proba"):
        counter[str(type(model))[8:-2]] = "unsupported"
        continue

    counter[str(type(model))[8:-2]] = 0
    for n in (5, 10, 25):
        for i in range(len(X_test)):
            row, row_value = X_test.iloc[i], Y_test.iloc[i]
            exp_in = explainer.explain_instance(
                X_test.iloc[i], model.predict_proba, num_features=2, num_samples=n
            )
            pred = (
                0
                if exp_in.predict_proba[0] > exp_in.predict_proba[1]
                else (1 if exp_in.predict_proba[0] < exp_in.predict_proba[1] else -1)
            )
            counter[str(type(model))[8:-2]] += 1 if pred == row_value["Class"] else 0

for k, v in counter.items():
    print(k, v / len(X_test) * 5 if isinstance(v, int) else v)


# SHAP

## Visualizations

In [ ]:
for pre, model in my_models:
    clear_output(wait=True)
    try:
        explainer = shap.LinearExplainer(model, X_train)
    except Exception as ex:
        print(ex)
        continue

    print(
        f"Model: {str(type(model))[8:-2]}\nExpected Value: {explainer.expected_value}"
    )
    shap_values = explainer.shap_values(X_test)
    # RAM intensive plot
    # display(shap.force_plot(explainer.expected_value, shap_values, X_test))
    shap.summary_plot(shap_values, X_test, X_test.columns)
    shap.decision_plot(explainer.expected_value, shap_values, X_test, link="logit")
    print("Negative")
    display(
        shap.force_plot(
            explainer.expected_value, shap_values[0], X_test.iloc[0], link="logit"
        )
    )
    # shap.bar_plot(shap_values[0], feature_names=X_test.columns, max_display=15)
    shap.plots._waterfall.waterfall_legacy(
        explainer.expected_value,
        shap_values[0],
        feature_names=X_test.columns,
        max_display=15,
    )
    print("Positive")
    display(
        shap.force_plot(
            explainer.expected_value, shap_values[7], X_test.iloc[7], link="logit"
        )
    )
    # shap.bar_plot(shap_values[7], feature_names=X_test.columns, max_display=15)
    shap.plots._waterfall.waterfall_legacy(
        explainer.expected_value,
        shap_values[7],
        feature_names=X_test.columns,
        max_display=15,
    )
    input("Just enjoy the results and press enter to continue")


## Stats

In [11]:
counter = dict()
for pre, model in my_models:
    counter[str(type(model))[8:-2]] = 0
    try:
        explainer = shap.Explainer(model, X_train)
    except Exception as ex:
        # print(ex)
        counter[str(type(model))[8:-2]] = "unsupported"
        continue

    if isinstance(explainer.expected_value, np.ndarray):
        counter[str(type(model))[8:-2]] = "unsupported"
        continue

    shap_values = explainer.shap_values(X_test)
    for i in range(len(X_test)):
        row_value = Y_test.iloc[i]
        pred = int(
            sum(shap_values[i]) + explainer.expected_value > explainer.expected_value
        )
        counter[str(type(model))[8:-2]] += 1 if pred == row_value["Class"] else 0

for k, v in counter.items():
    print(k, v / len(X_test) if isinstance(v, int) else v)


lightgbm.sklearn.LGBMClassifier 0.6744186046511628
sklearn.linear_model._ridge.RidgeClassifier 0.5813953488372093
sklearn.linear_model._logistic.LogisticRegression 0.5581395348837209
xgboost.sklearn.XGBClassifier 0.5581395348837209
sklearn.neighbors._classification.KNeighborsClassifier unsupported
sklearn.naive_bayes.GaussianNB unsupported
sklearn.discriminant_analysis.LinearDiscriminantAnalysis 0.5813953488372093
sklearn.ensemble._gb.GradientBoostingClassifier 0.7209302325581395
sklearn.ensemble._weight_boosting.AdaBoostClassifier unsupported
sklearn.linear_model._stochastic_gradient.SGDClassifier 0.5813953488372093
sklearn.ensemble._forest.RandomForestClassifier unsupported
sklearn.ensemble._forest.ExtraTreesClassifier unsupported
sklearn.tree._classes.DecisionTreeClassifier unsupported
sklearn.discriminant_analysis.QuadraticDiscriminantAnalysis unsupported


# ELI5

## Visualizations

In [ ]:
for pre, model in my_models:
    clear_output(wait=True)
    print(f"Model: {str(type(model))[8:-2]}")
    display(eli5.explain_weights(model, feature_names=X_test.columns.to_list()))
    print("Negative")
    display(eli5.explain_prediction(model, X_test.iloc[0], top=(25, 25)))
    print("Positive")
    display(eli5.explain_prediction(model, X_test.iloc[7], top=(25, 25)))
    input("Just enjoy the results and press enter to continue")


## Stats

In [12]:
counter = dict()
for pre, model in my_models:
    if eli5.explain_prediction_df(model, X_test.iloc[0], top=(25, 25)) is None:
        counter[str(type(model))[8:-2]] = "unsupported"
        continue

    counter[str(type(model))[8:-2]] = 0
    for i in range(len(X_test)):
        row, row_value = X_test.iloc[i], Y_test.iloc[i]
        counter[str(type(model))[8:-2]] += (
            1
            if eli5.explain_prediction_df(model, row, top=(25, 25))["target"].mode()[0]
            == row_value["Class"]
            else 0
        )

for k, v in counter.items():
    print(k, v / len(X_test) if isinstance(v, int) else v)


lightgbm.sklearn.LGBMClassifier 0.7441860465116279
sklearn.linear_model._ridge.RidgeClassifier 0.7209302325581395
sklearn.linear_model._logistic.LogisticRegression 0.7209302325581395
xgboost.sklearn.XGBClassifier 0.6976744186046512
sklearn.neighbors._classification.KNeighborsClassifier unsupported
sklearn.naive_bayes.GaussianNB unsupported
sklearn.discriminant_analysis.LinearDiscriminantAnalysis unsupported
sklearn.ensemble._gb.GradientBoostingClassifier 0.7674418604651163
sklearn.ensemble._weight_boosting.AdaBoostClassifier unsupported
sklearn.linear_model._stochastic_gradient.SGDClassifier 0.6744186046511628
sklearn.ensemble._forest.RandomForestClassifier 0.7441860465116279
sklearn.ensemble._forest.ExtraTreesClassifier 0.7209302325581395
sklearn.tree._classes.DecisionTreeClassifier 0.627906976744186
sklearn.discriminant_analysis.QuadraticDiscriminantAnalysis unsupported
